In [1]:
from sentence_transformers import SentenceTransformer, util
import numpy as np
import csv
import time
from os.path import isfile
import pandas as pd
import re
import spacy
import matplotlib.pyplot as plt
import Tools.processing as proc

nlp = spacy.load("en_core_web_sm")
model = SentenceTransformer('all-mpnet-base-v2')

/home/marcuswrrn/.local/lib/python3.10/site-packages/torch/cuda/__init__.py:107: UserWarning: CUDA initialization: CUDA unknown error - this may be due to an incorrectly set up environment, e.g. changing env variable CUDA_VISIBLE_DEVICES after program start. Setting the available devices to be zero. (Triggered internally at ../c10/cuda/CUDAFunctions.cpp:109.)
  return torch._C._cuda_getDeviceCount() > 0


In [2]:
chunk_size = 1000000

df_reader = pd.read_json("./Data_Storage/All_Amazon_Review.json", lines=True, chunksize=chunk_size)

In [3]:
def split_dataframe(df):
    # Initialize an empty dictionary to store the new DataFrames
    split_dfs = {}

    # Loop through the values 1 to 5
    for i in range(1, 6):
        # Filter the original DataFrame based on the "overall" column value and store it in the dictionary
        split_dfs[i] = df[df["overall"] == i]

    return split_dfs

df_one   = pd.DataFrame()
df_two   = pd.DataFrame()
df_three = pd.DataFrame()
df_four  = pd.DataFrame()
df_five  = pd.DataFrame()

for i, chunk in enumerate(df_reader):
    print(f"Iteration: {i}")
    dfs = split_dataframe(chunk)
    df_one = df_one.append(dfs[1])
    df_two = df_two.append(dfs[2])
    df_three = df_three.append(dfs[3])
    df_four = df_four.append(dfs[4])
    df_five = df_five.append(dfs[5])
    print(len(df_two))
    if (i >= 5):
        break
    if (len(df_two) >= 1000):
        break

Iteration: 0
55872


In [4]:
print(f"Five Stars: {len(df_five)}\nFour Stars: {len(df_four)}\nThree Stars: {len(df_three)}\nTwo Stars: {len(df_two)}\nOne Star: {len(df_one)}\n")

Five Stars: 600955
Four Stars: 150027
Three Stars: 79187
Two Stars: 55872
One Star: 113959



In [5]:
# Make sure that all dataframes have the same 
cutoff = len(df_two)

df5 = df_five.head(cutoff).reset_index()
df4 = df_four.head(cutoff).reset_index()
df3 = df_three.head(cutoff).reset_index()
df2 = df_two.head(cutoff).reset_index()
df1 = df_one.head(cutoff).reset_index()

In [6]:
df5.head()

index  overall  verified   reviewTime      reviewerID        asin  \
0      5        5     False  01 15, 2018  A3TXR8GLKS19RE  B017O9P72A   
1     11        5     False  12 25, 2017  A3KWZMO1A9TO3Z  B017O9P72A   
2     12        5     False  12 18, 2017  A1QBG1TTQZGJNM  B017O9P72A   
3     14        5     False  11 24, 2017  A2LNJJWW2TLL00  B017O9P72A   
4     22        5     False  06 29, 2017   ALBD3EW51P0PJ  B017O9P72A   

      reviewerName                                         reviewText  \
0            Nello                                        Great skill   
1  Amazon Customer  So easy to connect and I&rsquo;m having way to...   
2          Artyhow  I use &ldquo;Echo&rdquo; as the wake word.  I ...   
3          jarhead  I haven't had any issues  with this skill like...   
4   Mageswari Babu                                               Good   

                        summary  unixReviewTime vote image style  
0                         Great      1515974400  NaN   NaN   NaN  
1               This is awesome      1514160000    2   NaN   NaN  
2                Alexa and LIFX      1513555200    2   NaN   NaN  
3                      Love it!      1511481600  NaN   NaN   NaN  
4  Hooked it up today with ease      1498694400  NaN   NaN   NaN

In [7]:
def estimate_completion(iteration, total_iterations, start_time):
    elapsed_time = time.time() - start_time
    time_per_iteration = elapsed_time / iteration
    remaining_iterations = total_iterations - iteration
    estimated_completion_time = remaining_iterations * time_per_iteration
    return estimated_completion_time

def split_sentences(text: str):
    if type(text) != str:
        return None
    doc = nlp(text)
    return [sent.text.strip() for sent in doc.sents]

def column_mean(list_of_lists):
    # Convert the input list of lists to a numpy array
    data = np.array(list_of_lists)
    # Compute the mean average along the columns (axis=0)
    mean_average = np.mean(data, axis=0)
    # Convert the result back to a Python list
    mean_average_list = mean_average.tolist()
    return [mean_average_list]

encs = []
# Initialize the start time
start_time = time.time()
for i, text in enumerate(df1["reviewText"]):
    split_text = split_sentences(text)
    if split_text:
        encs.extend(model.encode(split_text))
        encs = column_mean(encs)
        remaining_time = estimate_completion(i + 1, cutoff, start_time)
        print(f"Iteration {i}/{cutoff}: Estimated time remaining: {remaining_time:.2f} seconds")


Iteration 0/55872: Estimated time remaining: 6303.16 seconds
Iteration 1/55872: Estimated time remaining: 4646.32 seconds
Iteration 2/55872: Estimated time remaining: 3848.81 seconds
Iteration 3/55872: Estimated time remaining: 3574.08 seconds
Iteration 4/55872: Estimated time remaining: 3384.61 seconds
Iteration 5/55872: Estimated time remaining: 3553.77 seconds
Iteration 6/55872: Estimated time remaining: 3472.56 seconds
Iteration 7/55872: Estimated time remaining: 3851.97 seconds
Iteration 8/55872: Estimated time remaining: 3665.88 seconds
Iteration 9/55872: Estimated time remaining: 3804.25 seconds
Iteration 10/55872: Estimated time remaining: 3647.15 seconds
Iteration 11/55872: Estimated time remaining: 3953.83 seconds
Iteration 12/55872: Estimated time remaining: 3900.89 seconds
Iteration 13/55872: Estimated time remaining: 3775.23 seconds
Iteration 14/55872: Estimated time remaining: 3667.58 seconds
Iteration 15/55872: Estimated time remaining: 3635.67 seconds
Iteration 16/55872

In [8]:
import json

df_pooled = pd.read_json("./Data_Storage/Processed_Data/Amazon_Pooled.json")
df_pooled["One_Star"] = encs

df_pooled.to_json("./Data_Storage/Processed_Data/Amazon_Pooled.json")

positive_enc = df_pooled["Five_Stars"][0]

In [10]:
sent = "I hate this product!"
encoding = model.encode(sent)
df_pooled2 = pd.read_json("/home/marcuswrrn/Projects/Semantic_Quantification/Semantic_Comparison/Data_Processing/Data/job_pooled_embeddings.json")
negative_enc = df_pooled["One_Star"]

positive = [float(enc) for enc in df_pooled2["positive"]]
negative = [float(enc) for enc in df_pooled2["negative"]]


print(util.cos_sim(positive_enc, encoding)[0][0])
print(util.cos_sim(negative_enc, encoding)[0][0])
print(util.cos_sim(positive, encoding)[0][0])
print(util.cos_sim(negative, encoding)[0][0])

tensor(0.3127)
tensor(0.2953)
tensor(0.0801)
tensor(0.1763)
